<a href="https://colab.research.google.com/github/ohashin2/Dataset/blob/master/test.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Exploring HTR3A protein target activity data from ExcapeDB

The Target specific data was downloaded from https://zenodo.org/record/173258#.X_44kuhKi70

Please refer to the ExCAPE-DB publication (https://pubmed.ncbi.nlm.nih.gov/28316655/) for details about the database 

Here are some details about HTR3A gene (taken from RefSeq NCBI)
*The product of this gene belongs to the ligand-gated ion channel receptor superfamily. This gene encodes subunit A of the type 3 receptor for 5-hydroxytryptamine (serotonin), a biogenic hormone that functions as a neurotransmitter, a hormone, and a mitogen. This receptor causes fast, depolarizing responses in neurons after activation. It appears that the heteromeric combination of A and B subunits is necessary to provide the full functional features of this receptor, since either subunit alone results in receptors with very low conductance and response amplitude. Alternatively spliced transcript variants encoding different isoforms have been identified.*

Diseases associated with HTR3A include Irritable Bowel Syndrome and Motion Sickness.

## Basic information about HTR3A gene:

**Present in** Chromosome 11
**Exon count:** 10

mRNA and protein information

*   NM_000869.6 → NP_000860.3 
*   NM_001161772.3 → NP_001155244.1
*   NM_213621.4 → NP_998786.3 








# Before you begin, make sure you close all other COLAB notebooks. 

# Change Runtime settings

## Plesae change your runtime settings to use GPU and high-memory, if you have 

## Runtime --> Change Runtime Type --> GPU wityh high-RAM

In [1]:
!date # starting time

Mon Feb 15 18:53:23 UTC 2021


## Install AMPL GPU version

```
real	2m59.739s
user	1m48.995s
sys	0m20.614s
```

In [2]:
import requests

# Copy AMPL install script
url='https://raw.githubusercontent.com/ravichas/AMPL-Tutorial/master/config/install_AMPL_GPU.sh'

downloaded_obj = requests.get(url)
with open("install_AMPL_GPU.sh", "wb") as file:
    file.write(downloaded_obj.content)


# Install and load AMPL
!chmod u+x install_AMPL_GPU.sh
!time ./install_AMPL_GPU.sh
import sys
if '/content/AMPL/lib/python3.6/site-packages' not in sys.path:
    sys.path.insert(1, '/content/AMPL/lib/python3.6/site-packages')

sys.path

--2021-02-15 18:53:25--  https://repo.anaconda.com/miniconda/Miniconda3-latest-Linux-x86_64.sh
Resolving repo.anaconda.com (repo.anaconda.com)... 104.16.131.3, 104.16.130.3, 2606:4700::6810:8303, ...
Connecting to repo.anaconda.com (repo.anaconda.com)|104.16.131.3|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 94235922 (90M) [application/x-sh]
Saving to: ‘Miniconda3-latest-Linux-x86_64.sh’

Miniconda3-latest-L 100%[===================>]  89.87M   221MB/s    in 0.4s    

2021-02-15 18:53:25 (221 MB/s) - ‘Miniconda3-latest-Linux-x86_64.sh’ saved [94235922/94235922]

PREFIX=/content/AMPL
Unpacking payload ...
Solving environment: - \ done

## Package Plan ##

  environment location: /content/AMPL

  added / updated specs:
    - _libgcc_mutex==0.1=main
    - brotlipy==0.7.0=py38h27cfd23_1003
    - ca-certificates==2020.10.14=0
    - certifi==2020.6.20=pyhd3eb1b0_3
    - cffi==1.14.3=py38h261ae71_2
    - chardet==3.0.4=py38h06a4308_1003
    - conda-package-han

['',
 '/content/AMPL/lib/python3.6/site-packages',
 '/env/python',
 '/usr/lib/python36.zip',
 '/usr/lib/python3.6',
 '/usr/lib/python3.6/lib-dynload',
 '/usr/local/lib/python3.6/dist-packages',
 '/usr/lib/python3/dist-packages',
 '/usr/local/lib/python3.6/dist-packages/IPython/extensions',
 '/root/.ipython']

## Exploring target activity data from selected database
## Data source = ExcapeDB
## Target activity for the receptor HTR3A

In [6]:
# There is a problem with the previously imported cffi, so delete it and 
# load it with AMPL instead
if 'cffi' in sys.modules:
  del sys.modules['cffi']

In [7]:
# We temporarily disable warnings for demonstration.
# FutureWarnings and DeprecationWarnings are present from some of the AMPL 
# dependency modules.
import warnings
warnings.filterwarnings('ignore')

import json
# import numpy as np
# import pandas as pd
import os
import requests

In [8]:
#
# Import AMPL libraries
# 
import atomsci.ddm.utils.data_curation_functions as dcf
import atomsci.ddm.utils.curate_data as curate_data
import atomsci.ddm.pipeline.diversity_plots as dp
import atomsci.ddm.pipeline.chem_diversity as cd
# Additional python libraries
import pandas as pd
import numpy as np
import getpass,os

## Select a target to work with 
### (e.g. PDE2A, KCNH2, SCNA5)

In [9]:
target_name='HTR3A'

ofile=target_name+'_excape_curated.csv'

# Define data locations 
## get username to use as a unique identifier to work in shared directories

In [10]:
# ofile=target_name+'_excape_curated.csv'
ofile=target_name+'_excape.csv'

In [13]:
import io
url = 'https://raw.githubusercontent.com/ohashin2/Dataset/master/ACHE_ChEMBL_TSV_2021-02-13.tsv'
# url = 'https://raw.githubusercontent.com/ravichas/AMPL-Tutorial/master/datasets/Excape_HTR3A.tsv'
download = requests.get(url).content

In [14]:
download

b'"Molecule ChEMBL ID"\t"Molecule Name"\t"Molecule Max Phase"\t"Molecular Weight"\t"#RO5 Violations"\t"AlogP"\t"Compound Key"\t"Smiles"\t"Standard Type"\t"Standard Relation"\t"Standard Value"\t"Standard Units"\t"pChEMBL Value"\t"Data Validity Comment"\t"Comment"\t"Uo Units"\t"Ligand Efficiency BEI"\t"Ligand Efficiency LE"\t"Ligand Efficiency LLE"\t"Ligand Efficiency SEI"\t"Potential Duplicate"\t"Assay ChEMBL ID"\t"Assay Description"\t"Assay Type"\t"BAO Format ID"\t"BAO Label"\t"Assay Organism"\t"Assay Tissue ChEMBL ID"\t"Assay Tissue Name"\t"Assay Cell Type"\t"Assay Subcellular Fraction"\t"Target ChEMBL ID"\t"Target Name"\t"Target Organism"\t"Target Type"\t"Document ChEMBL ID"\t"Source ID"\t"Source Description"\t"Document Journal"\t"Document Year"\t"Cell ChEMBL ID"\n"CHEMBL14598"\t""\t"0"\t"386.43"\t"0"\t"2.35"\t"1k"\t"COc1ccc(C(=O)/C(=N/O)SCCCN(C)C)cc1.O=C(O)C(=O)O"\t"IC50"\t""\t""\t""\t""\t""\t"Not Determined"\t""\t""\t""\t""\t""\t"False"\t"CHEMBL644103"\t"Compound was evaluated for 

In [17]:
# Reading the downloaded content and turning it into a pandas dataframe
orig_df = pd.read_csv(io.StringIO(download.decode('utf-8')), sep='\t' )

In [18]:
orig_df

Molecule ChEMBL ID Molecule Name  ...  Document Year Cell ChEMBL ID
0            CHEMBL14598           NaN  ...         1986.0           None
1           CHEMBL496946           NaN  ...         2008.0           None
2           CHEMBL508778           NaN  ...         2008.0           None
3           CHEMBL496127           NaN  ...         2008.0           None
4               CHEMBL95       TACRINE  ...         2008.0           None
...                  ...           ...  ...            ...            ...
13475      CHEMBL4282360           NaN  ...         2018.0           None
13476      CHEMBL4285213           NaN  ...         2018.0           None
13477      CHEMBL4282163           NaN  ...         2018.0           None
13478          CHEMBL502     DONEPEZIL  ...         2018.0           None
13479      CHEMBL4279488           NaN  ...         2018.0           None

[13480 rows x 41 columns]

In [ ]:
!date # ending time

Fri Feb 12 14:54:35 UTC 2021
